In [1]:
%load_ext autoreload
%autoreload 2

In [17]:
import re
import rules.v04_Rac1_dominant_mod as rul
from rules.enzymes_v04 import *
import itertools

group_name = re.sub(".+\.", "", rul.__name__)

all_nodes = {
    Arp2_3, CP, Cdc42, Cofilin, Coronin, Cortactin, Dia1, Dia2, Ena_Vasp,
    IRSp53_Cdc42, IRSp53_Rac1, LIMK, PAK, PIP2, PKD, Profilin, ROCK, 
    ARHGAP22, NET1, ROS, 
    Rac1, RhoA, SSH, Thymosin, WASP, WAVE
}

rules_map = {}
orig_rules = rul.build_rules()
rules_map['base'] = orig_rules

# # knockdowns
# for nodes in sorted([{a, b} for a, b in itertools.combinations_with_replacement(sorted(all_nodes), 2)]):
# for nodes in [{Thymosin, WASP}, {Thymosin, WAVE}, {WASP, WAVE}]:
for nodes in [{n} for n in all_nodes]:
# for nodes in []:
    graph = orig_rules["graph"].copy()
    rules = orig_rules['rules']

    for node in nodes:
        graph.remove_edges_from([(node, target)
                                 for target in list(graph[node])])
        rules = re.sub('1:\s*' + node + '\*\s*=.+', '', rules)
        rules = rules + '1: ' + node + '* = False \n'

    rules_map["del_" + "_".join(sorted(nodes))] = {
        "graph": graph,
        "rules": rules
    }

print("Group name: {}".format(group_name))
sorted(rules_map.keys())


Group name: v04_Rac1_dominant_mod


['base',
 'del_ARHGAP22',
 'del_Arp2_3',
 'del_CP',
 'del_Cdc42',
 'del_Cofilin',
 'del_Coronin',
 'del_Cortactin',
 'del_Dia1',
 'del_Dia2',
 'del_Ena_Vasp',
 'del_IRSp53_Cdc42',
 'del_IRSp53_Rac1',
 'del_LIMK',
 'del_NET1',
 'del_PAK',
 'del_PIP2',
 'del_PKD',
 'del_Profilin',
 'del_ROCK',
 'del_ROS',
 'del_Rac1',
 'del_RhoA',
 'del_SSH',
 'del_Thymosin',
 'del_WASP',
 'del_WAVE']

In [ ]:
### run selected rules
%run params.ipynb

for name, rules in sorted(rules_map.items()):
    print("\n\n====== {} - {}".format(group_name, name))    
    PARAMS['group'] = group_name
    PARAMS['name'] = name    
    PARAMS['save_file'] = True
    PARAMS['graph'] = rules['graph']
    PARAMS['rules'] = rules['rules']
    PARAMS['chunk_size'] = 64
    PARAMS['chunks'] = 16 #156
    PARAMS['report_basins'] = [[Actin_BR, Actin_ST], [Rac1, RhoA]]
    PARAMS['rewrite'] = False
    
    %run "01. structural analysis.ipynb"        
    %run "02. build basins.ipynb"
    %run "03. analyse basins.ipynb"



====== v04_Rac1_dominant_mod - base
Saving dependecny matrix for base
Running boolean simulations on 16 CPUs


In [8]:
# build summary for selected rules map
import os
import pandas as pd
import numpy as np

def color_delta(src):
    base = src['base']
    if base == 0:
        colors = ['black'] * len(src)
    else:
        colors = [ 'red' if s > 1.2 else 'blue' if s < 0.8 else 'black' for s in src / base]    
    return [ 'color: {}'.format(c)  for c in colors]

cases = sorted(rules_map.keys())
rep = pd.read_csv("reports/"+group_name+"/"+cases[0]+"/weighted_activity.csv", index_col=0)
rep.columns = ["base"]
for case in cases[1:]:
    file_name = "reports/"+group_name + "/"+ case+"/weighted_activity.csv"
    if os.path.isfile(file_name):
        name = re.sub("del_", "", case)
        rep[name] = pd.read_csv(file_name, index_col=0).iloc[:, 0].rename(name)

rep['mean'] = rep.mean(axis=1)
rep.to_csv("reports/"+group_name+"/summary.csv")

styler = rep.style.apply(color_delta, axis=1)

with open('reports/'+group_name+'/summary.html', 'w') as fo:
    fo.write(styler.render())
    
print("Group name: {}".format(group_name))
styler

Group name: v04_RhoA_dominant


In [9]:
# build double knockdown summary for selected rules map
import pandas as pd
import numpy as np
import os.path

def color_delta(src, base):
    if src.name[1] == 'BR':
        b = base[0]
    else:
        b = base[1]
        
    if b == 0:        
        colors = ['black'] * len(src)
    else:
        colors = [ 'gray' if pd.isnull(s) else 'red' if s > 1.2 else 'blue' if s < 0.8 else 'black' for s in src / b]  
    return [ 'color: {}'.format(c)  for c in colors]


na = 'n/a'
BR = 'BR'
ST = 'ST'
midx = pd.MultiIndex.from_product([[na] + sorted(all_nodes), [BR, ST]])
report = pd.DataFrame(index=midx, columns=[na] + sorted(all_nodes), data=None)

cases = sorted(rules_map.keys())

#base
rep = pd.read_csv("reports/"+group_name+"/"+cases[0]+"/weighted_activity.csv", index_col=0)
base_BR = rep['activity, %']['Actin_BR']
base_ST = rep['activity, %']['Actin_ST']
report[na][na] = (base_BR, base_ST)

node_re = '|'.join(all_nodes)

for case in cases[1:]:
    file_name = "reports/"+group_name+"/"+case+"/weighted_activity.csv"   
    if os.path.isfile(file_name):               
        name = re.sub("del_", "", case)    
        match = re.match("("+node_re+")(_("+node_re+"))?", name) 
        a, b = match.group(1, 3)
        if b is None:
            b = na
        
        rep = pd.read_csv(file_name, index_col=0)
        values = (rep['activity, %']['Actin_BR'], rep['activity, %']['Actin_ST'])
        report[a][b] = values
        report[b][a] = values        


report.to_csv("reports/"+group_name+"/double_knockdown_summary.csv")       
styler = report.style.apply(color_delta, axis=1, base=(base_BR, base_ST))

additional_style= """
<style type="text/css">
table { border-collapse: collapse; }
thead { border-bottom: solid 1px black; }
tbody > tr:nth-child(2n + 3) { border-top: solid 1px black; }
tbody > tr:nth-child(4n - 2), tbody > tr:nth-child(4n - 3) { background-color: #eee; }
.data, .col_heading {
    border-left: solid 1px black;
    padding-left: 0.3rem;
    padding-right: 0.3rem;
    text-align: center;
}
</style>
"""

with open('reports/'+group_name+'/double_knockdown_summary.html', 'w') as fo:
    fo.write("<html><body>"+additional_style + styler.render()+"</body></html>")
    
styler